In [ ]:
# using PyTorch-2.0.1
# using PyTorch-2.0.1
# using PyTorch-2.0.1

In [2]:
import os

!pwd
os.chdir('/home/sunhuaikuan/ondemand/blue_DNABERT_2/triton/python')

!pwd
# !pip install cmake
# !pip install -e .
!python setup.py install 

# !pip install triton
# !python3 -m pip install -r requirements.txt

/blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python
/blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python
copy /home/sunhuaikuan/.triton/nvidia/ptxas/bin/ptxas to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/backend/bin/ptxas ...
copy /home/sunhuaikuan/.triton/nvidia/cuobjdump/bin/cuobjdump to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/backend/bin/cuobjdump ...
copy /home/sunhuaikuan/.triton/nvidia/nvdisasm/bin/nvdisasm to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/backend/bin/nvdisasm ...
copy /home/sunhuaikuan/.triton/nvidia/cudacrt/include to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/backend/include ...
copy /home/sunhuaikuan/.triton/nvidia/cudart/include to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/backend/include ...
copy /home/sunhuaikuan/.triton/nvidia/cupti/include to /blue/xiaofan/sunhuaikuan/DNABERT_2/triton/python/../third_party/nvidia/ba

In [2]:
# !nvcc --version
# !pip install torch torchvision torchaudio --extra-index-url https://download.pytorch.org/whl/cu123

In [26]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
from sklearn.preprocessing import StandardScaler
import torch
from transformers import AutoTokenizer, AutoModel,BertConfig

from tqdm import tqdm

# import pickle
# import re
import os
import csv
import warnings
warnings.filterwarnings('ignore')

os.chdir('/home/sunhuaikuan/ondemand/blue_papers/DNA_LLM_REVIEW/embeddings/methylation')
%run preprocess_utility.py

device=torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

In [4]:
tokenizer = AutoTokenizer.from_pretrained("zhihan1996/DNABERT-2-117M", trust_remote_code=True)
model = AutoModel.from_pretrained("zhihan1996/DNABERT-2-117M", trust_remote_code=True).to(device)
# tokenizer = AutoTokenizer.from_pretrained("zhihan1996/DNABERT-2-117M", trust_remote_code=True, revision="1c51eccc93c384e4ded6a71055ac360d0cf68196")
# model = AutoModel.from_pretrained("zhihan1996/DNABERT-2-117M", trust_remote_code=True, revision="1c51eccc93c384e4ded6a71055ac360d0cf68196")

Some weights of the model checkpoint at zhihan1996/DNABERT-2-117M were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.bias', 'cls.predictions.transform.LayerNorm.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertModel were not initialized from the model checkpoint at zhihan1996/DNABERT-2-117M and are newly initialized: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
You should prob

### Load Human Chrom Sequences from .fa File

In [16]:
# def read_fasta(fasta_file):
#     sequences = {}
#     sequence_name = ''
#     sequence_data = []
    
#     file_handle=open(fasta_file, 'r')
#     file_handle.seek(0)

#     for line in file_handle:
#             line = line.strip()
#             if line.startswith('>'):
#                 if sequence_name:
#                     sequences[sequence_name] = ''.join(sequence_data)
#                 sequence_name = line[1:]  # Remove the '>' character
#                 sequence_data = []
#             else:
#                 sequence_data.append(line)
        
#     if sequence_name:
#             sequences[sequence_name] = ''.join(sequence_data)
    
#     file_handle.close()
    
#     return sequences

fasta_file = "/blue/xiaofan/sunhuaikuan/gpn/examples/msa/genome.hg38rg.fa"
chrom_sequences = read_fasta(fasta_file)

In [17]:
# def get_embedding(dna):

#     # dna = "ACGTAGCATCGGATCTATCTATCGACACTTGGTTATCGATCTACGAGCATCTCGTTAGC"
#     inputs = tokenizer(dna, return_tensors = 'pt')["input_ids"].to(device)
#     # print(inputs)
#     hidden_states = model(inputs)[0] # [1, sequence_length, 768]
    
    
#     # embedding with mean pooling
#     embedding_mean = torch.mean(hidden_states[0], dim=0)
#     # print(embedding_mean.shape) # expect to be 768
#     # print(embedding_mean)
#     # embedding with max pooling
#     embedding_max = torch.max(hidden_states[0], dim=0)[0]
#     # print(embedding_max.shape) # expect to be 768
#     # print(embedding_max)
    
#     return embedding_max



def get_embedding(dna):

    # dna = "ACGTAGCATCGGATCTATCTATCGACACTTGGTTATCGATCTACGAGCATCTCGTTAGC"
    inputs = tokenizer(dna, return_tensors = 'pt')["input_ids"].to(device)
    # with torch.no_grad():
    #     hidden_states = model(inputs)[0] 
    #     last_hidden_state = hidden_states.last_hidden_state

    # # Extract the [CLS] embedding
    # cls_embedding = last_hidden_state[:, 0, :]


    with torch.no_grad():
        hidden_states = model(inputs)[0]  # Get model outputs
        last_hidden_state = hidden_states[0]  # Access the last hidden state directly

    # print(last_hidden_state.shape)

    # Extract the [CLS] embedding
    cls_embedding = last_hidden_state[0, :]  # Extract the [CLS] embedding

    # cls_embedding = cls_embedding.to(torch.float32)
    
    return cls_embedding


In [18]:
def get_subsequence(chrom_name, start_pos, length):
    
    # print(chrom_name, start_pos, length)
    if chrom_name in chrom_sequences:
        sequence = chrom_sequences[chrom_name]
        subsequence = sequence[start_pos:start_pos + length]
        return subsequence
    else:
        raise ValueError(f"Chromosome '{chrom_name}' not found in the FASTA file.")

In [8]:
# def PreProcess(data_filename):
#     # df=pd.read_csv(data_filename, delimiter='\t',  names=['CHROM', 'POS', 'REF','ALT','INFO'])
#     df=pd.read_csv(data_filename, header=0, sep='\t', index_col=None)   # With head column row

#     df=df[(df['REF'].str.len() == 1) & (df['ALT'].str.len() == 1)]
#     df['CHROM'] = df['CHROM'].str.replace('chr', '')
#     df['y']=0
#     df.drop(columns=['Consequence'], inplace=True)
#     return df

In [19]:
# def append_rows_to_csv(csv_Filename, rows):
#     with open(csv_Filename, mode='a', newline='') as file:
#         writer = csv.writer(file)
#         # writer.writerow(rows)
#         for row in rows:
#             writer.writerow(row)

In [20]:
!pwd

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
/blue/xiaofan/sunhuaikuan/PAPERS/DNA_LLM_REVIEW/embeddings/methylation


In [22]:
# datafile='clinvar_20240805.noncoding'
# datafile='clinvar_20240805.missense_matched'
datafile='methylation'

In [23]:
%%time

os.chdir('/home/sunhuaikuan/ondemand/blue_DNABERT_2')

comp = {'A':1, 'C':2, 'G':3, 'T':4}

max_length=512


# csv_Filename = datafile + '_with_embedding.csv'
# if os.path.exists(csv_Filename):
#     os.remove(csv_Filename)

max_length= 128 # 186

import gzip
import pandas as pd

max_length= 128 # 186


# Open the gzipped file and read it into a DataFrame
with gzip.open('GSM6637962_CpG_coverage20_GRCh38.bed.gz', 'rt') as f:
    df = pd.read_csv(f, sep='\t')  # Automatically detects header from the file


df['CHROM'] = df['CHROM'].str.replace('chr', '', regex=False)

df['START']=df['FROM']- max_length //2 -1

# df['END']=df['START'] + max_length


# df['REF']='A'
# df['ALT']='A'
df['SIZE']=max_length

df = df.rename(columns={'Percentage':'y'})
df = df.drop(['FROM','TO','Coverage'], axis=1)


cols = df.columns.tolist()

# Move the 3rd column to the last position
cols.append(cols.pop(1))

# Reorder the DataFrame
df = df[cols]
df=df[~df['CHROM'].str.contains('KI',na=False)]
df=df[~df['CHROM'].str.contains('GL',na=False)]
df=df[~df['CHROM'].str.contains('M',na=False)]

df

CPU times: user 75.8 ms, sys: 4.16 ms, total: 80 ms
Wall time: 115 ms


CHROM     START REF ALT  SIZE    y
0         1    788342   A   A   128  100
1         1    788407   A   A   128   80
2         1    788760   A   A   128   95
3         1    788779   A   A   128   90
4         1    788794   A   A   128  100
...     ...       ...  ..  ..   ...  ...
54789     Y  56870838   A   A   128   65
54790     Y  56870918   A   A   128   17
54791     Y  56871044   A   A   128   34
54792     Y  56871437   A   A   128    0
54793     Y  56873834   A   A   128   36

[47953 rows x 6 columns]

### Main Process

In [28]:
%%time

csv_Filename = datafile + '_dnabert2_embedding.csv'
if os.path.exists(csv_Filename):
    os.remove(csv_Filename)


rows=[]
for index, row in df.iterrows():      
    chrom=row['CHROM']
    # pos=row['POS']
    # pos_start=row['POS']-round(max_length / 2)
    pos_start=row['START']
    if pos_start<=1:
        pos_start=1
    # ref=row['REF']
    # alt=row['ALT']        
    # info=row['INFO']
    y=row['y']
    length = row['SIZE']
    
    subsequence = get_subsequence(chrom, pos_start, length)
    if 'N' in subsequence:
        print("The character 'N' is present in the string.")
        
    embedding = get_embedding(subsequence)
    # print(embedding.shape)
    # print (embedding)

    # feature=np.array(embedding_df.iloc[64])
    rows.append(np.append(embedding.cpu().detach().numpy(),  [ y]))  # chrom, comp[ref],comp[alt], length, 


    if ((index % 5000) ==0):
        append_rows_to_csv(csv_Filename, rows)
        rows=[]
        print (f"index = {index} completed")
        
append_rows_to_csv(csv_Filename, rows)

print(f"Create File: "+csv_Filename)
    

index = 0 completed
index = 5000 completed
index = 10000 completed
index = 15000 completed
The character 'N' is present in the string.
index = 20000 completed
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
The character 'N' is present in the string.
index = 25000 completed
The character 'N' is present in the string.
index = 30000 completed
The character 'N' is present in the string.
index = 35000 completed
index = 40000 completed
The character 'N' is present in the string.
The character 'N' is present in the string.
index = 45000 completed
Create File: methylation_with_embedding.csv
CPU times: user 8

### Load CSV File

In [29]:
df = load_embedding_file(csv_Filename)
df

1         2         3         4         5         6         7  \
0     -0.083390 -0.258933 -0.243736 -0.068575  0.046474 -0.116321 -0.029331   
1     -0.061488  0.254779 -0.087146  0.229627 -0.184495  0.192147  0.189369   
2     -0.136037  0.144205 -0.152447  0.235368 -0.000172  0.160265  0.291557   
3     -0.104312  0.012862 -0.065762  0.204776  0.084184  0.136624  0.203835   
4     -0.021077  0.039501 -0.032483  0.042059  0.189386  0.217917  0.131305   
...         ...       ...       ...       ...       ...       ...       ...   
47947 -0.149953 -0.182523 -0.012265 -0.336270 -0.501324  0.060049  0.241617   
47948  0.052923 -0.075620  0.009705 -0.179491 -0.158333  0.012871  0.091000   
47949  0.008553 -0.023487  0.063686  0.143789 -0.418942 -0.156553  0.286688   
47950 -0.298390  0.097165  0.143236  0.119553 -0.160728 -0.010775  0.192235   
47951  0.030048 -0.079840  0.053093 -0.218059 -0.330208 -0.140608  0.273048   

              8         9        10  ...       760       761       762  \
0     -0.349223 -0.159346 -0.138453  ... -0.003283  0.056232 -0.109179   
1     -0.449269  0.077489 -0.176105  ... -0.318612 -0.139309  0.113252   
2     -0.515609  0.068223 -0.105480  ... -0.426330 -0.128075  0.072868   
3     -0.496195  0.013240 -0.104256  ... -0.363405 -0.091254  0.067492   
4     -0.523507 -0.114336 -0.112766  ... -0.306083 -0.098057  0.003412   
...         ...       ...       ...  ...       ...       ...       ...   
47947 -0.138011 -0.261802 -0.033976  ... -0.287817 -0.124544  0.074238   
47948  0.019514 -0.199830  0.236948  ... -0.290156 -0.117208  0.002011   
47949 -0.046593 -0.049523  0.184708  ... -0.075285 -0.075534  0.092570   
47950 -0.028392  0.039537  0.086717  ... -0.167683  0.006252  0.247534   
47951  0.103369  0.061450  0.208826  ... -0.205512  0.158370  0.035516   

            763       764       765       766       767       768      y  
0     -0.050083  0.041217 -0.015485  0.241385  0.082229 -0.031224   80.0  
1     -0.185463 -0.006996  0.316996  0.094948 -0.066948  0.447760   95.0  
2     -0.133047 -0.014383  0.263468  0.045382  0.033886  0.408537   90.0  
3     -0.132907 -0.018070  0.228073  0.146403  0.111401  0.265670  100.0  
4     -0.286123 -0.131211  0.229164  0.269820  0.241063  0.263663   96.0  
...         ...       ...       ...       ...       ...       ...    ...  
47947 -0.287959  0.176460  0.126452  0.102711 -0.027036 -0.014746   65.0  
47948 -0.452492 -0.017481  0.041878  0.271162 -0.053284  0.312605   17.0  
47949  0.057646  0.314604  0.104889  0.366008  0.052773  0.020643   34.0  
47950 -0.285400 -0.169548  0.281239  0.334298  0.203064 -0.094630    0.0  
47951 -0.065131  0.108087  0.092537  0.488766  0.308329 -0.445665   36.0  

[47952 rows x 769 columns]

In [17]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 95759 entries, 0 to 95758
Columns: 773 entries, 1 to y
dtypes: float64(768), int64(4), object(1)
memory usage: 564.7+ MB


In [4]:
# !pip show transformers  triton torch
!pip list

Package                   Version
------------------------- ---------------
antlr4-python3-runtime    4.9.3
anyio                     4.3.0
argon2-cffi               23.1.0
argon2-cffi-bindings      21.2.0
arrow                     1.3.0
asttokens                 2.4.1
async-lru                 2.0.4
attrs                     23.2.0
Babel                     2.14.0
beautifulsoup4            4.12.3
biopython                 1.84
bleach                    6.1.0
boto3                     1.34.45
botocore                  1.34.45
Brotli                    1.0.9
cached-property           1.5.2
certifi                   2024.2.2
cffi                      1.16.0
charset-normalizer        3.3.2
comm                      0.2.1
contourpy                 1.2.0
cycler                    0.12.1
debugpy                   1.8.1
decorator                 5.1.1
defusedxml                0.7.1
einops                    0.8.0
entrypoints               0.4
exceptiongroup            1.2.0
executing        